In [1]:
# !pip install -q geopandas
# !pip install -q geopy

In [2]:
import pandas as pd
df = pd.read_csv('web_data.csv')
df.drop_duplicates(keep='first', inplace=True)
df.tail()

Category                                           Location  \
11052         Commenting                  Trains mumbai, Maharashtra, India   
11053         Commenting  Kemps Corner, Malabar Hill, Mumbai, Maharashtr...   
11054  Touching /Groping  New Delhi, Bhavbhuti Marg, Kamla Market, Ajmer...   
11055  Touching /Groping                        Kibera slum, Nairobi, Kenya   
11056  Touching /Groping                        Kibera slum, Nairobi, Kenya   

                                                Incident  
11052   Stalking,touching,commenting,grouping during ...  
11053   Looked straight at me and banged into me.Didn...  
11054   I was on the escalator and suddenly someone t...  
11055   a girl was sent by her father to go buy a pas...  
11056   a girl is coming from a poor family and had s...

In [3]:
from geopy.geocoders import Nominatim
from geopy.extra.rate_limiter import RateLimiter
from tqdm import tqdm

geolocator = Nominatim(timeout=10, user_agent="my-app")
geocode = RateLimiter(geolocator.geocode, min_delay_seconds=1)

add = []
lat = []
lon = []
cat = []
inc = []

for id, row in tqdm(df.iterrows(), total=len(df)):
  loc = row['Location']
  if 'India' not in loc: 
    continue
  idx = -5
  while idx < -1:
    addr = ", ".join(loc.split(', ')[idx:])
    coord = geocode(addr)
    if coord is not None:
      add.append(loc)
      lat.append(coord.latitude)
      lon.append(coord.longitude)
      cat.append(row['Category'])
      inc.append(row['Incident'])
      break
    idx+=1

100%|██████████████████████████████████████████████████████████████████████████| 10229/10229 [3:06:06<00:00,  1.09s/it]


In [4]:
new_df = pd.DataFrame(list(zip(add, lat, lon, cat, inc)),
columns=['Address', 'Latitude', 'Longitude', 'Category', 'Incident'])

In [5]:
new_df.to_csv('crime_data.csv', index=False)

In [6]:
import folium

map1 = folium.Map(
    location=[21,78],
    tiles='cartodbpositron',
    zoom_start=5,
)
new_df.apply(lambda row:folium.CircleMarker(location=[row["Latitude"], row["Longitude"]]).add_to(map1), axis=1)
map1


In [7]:
new_df.shape

(6343, 5)